In [1]:
import pandas as pd
import plotly.express as px

pd.options.plotting.backend = "plotly"

### Read sensors data file

In [2]:
sensors_data_file = 'S1-ADL1_sensors_data.txt.new.csv'

df = pd.read_csv(sensors_data_file)

# Set Millisec column to index
df.set_index(df.columns[0], inplace=True)

# Divide by 1000 to convert from milliseconds to seconds
df.index = df.index / 1000
df.index.name = '1 SECOND'

C:\Users\Admin\AppData\Local\Temp\ipykernel_7652\2744205504.py:3: DtypeWarning: Columns (243,244,245,246,247,248,249) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(sensors_data_file)


### Plot some columns against time

In [3]:
fig = px.line(df.iloc[:, 0:5], title=sensors_data_file.split('.')[0], labels=dict(index="Time (s)", variable="Column Name", value="Value"))
fig.update_traces(mode="lines", hovertemplate='%{y}')
fig.update_layout(hovermode="x unified")

fig.show()

### Dash app with selectable columns

In [13]:
from dash import Dash, html, dcc, callback, Output, Input
import itertools

acc_list = [
    "RKN^",
    "HIP",
    "LUA^",
    "RUA_",
    "LH",
    "BACK",
    "RKN_",
    "RWR",
    "RUA^",
    "LUA_",
    "LWR",
    "RH",
]

imu_list = [
    "BACK",
    "RUA",
    "RLA",
    "LUA",
    "LLA",
]

imu_shoe_list = [
    "L-SHOE",
    "R-SHOE",
]

column_list = (
    [f"Acc {acc}" for acc in acc_list]
    + list(
        itertools.chain(
            *[[f"IMU {imu} acc", f"IMU {imu} gyro", f"IMU {imu} magnetic", f"IMU {imu} Quaternion"] for imu in imu_list]
        )
    )
    + list(
        itertools.chain(
            *[
                [
                    f"IMU {imu} Eu",
                    f"IMU {imu} Nav_A",
                    f"IMU {imu} Body_A",
                    f"IMU {imu} AngVelBodyFrame",
                    f"IMU {imu} AngVelNavFrame",
                    f"IMU {imu} Compass",
                ]
                for imu in imu_shoe_list
            ]
        )
    )
)


app = Dash(__name__, external_stylesheets=["https://codepen.io/chriddyp/pen/bWLwgP.css"])

app.layout = html.Div(
    [
        dcc.Dropdown(column_list, ["IMU RUA Quaternion", "IMU LUA Quaternion"], multi=True, id="dropdown-selection"),
        dcc.Checklist(
            options={"X": "X axis", "Y": "Y axis", "Z": "Z axis", "W": "W axis"},
            value=["X", "Y", "Z", "W"],
            inline=True,
            id="checklist-selection",
        ),
        dcc.Graph(id="graph-content"),
        dcc.RangeSlider(
            min=0,
            max=df.last_valid_index(),
            step=1,
            value=[0, 600],
            marks={0: "0", df.last_valid_index(): f"{df.last_valid_index()}"},
            tooltip={"placement": "bottom", "always_visible": True},
            id="my-range-slider",
        ),
    ]
)


@callback(
    Output("graph-content", "figure"),
    Input("dropdown-selection", "value"),
    Input("checklist-selection", "value"),
    Input("my-range-slider", "value"),
)
def update_graph_dropdown(dropdown_values, checklist_values, slider_range):
    checklist_indices = dict(map(reversed, enumerate(["X", "Y", "Z", "W"])))
    checklist_values_quat = [checklist_indices[x] for x in checklist_values]

    dff = df[
        [
            col
            for col in df.columns
            if any([val in col for val in dropdown_values])
            and (
                col.endswith(tuple(checklist_values))
                or col.endswith(tuple(["Quaternion" + str(i + 1) for i in checklist_values_quat]))
            )
        ]
    ]

    fig = px.line(
        dff.loc[slider_range[0] : slider_range[1]],
        title=sensors_data_file.split(".")[0],
        labels=dict(variable="Column Name", value="Value"),
    )
    fig.update_traces(mode="lines", hovertemplate="%{y}")
    fig.update_layout(hovermode="x unified", xaxis_title="Time (s)")

    return fig


if __name__ == "__main__":
    app.run(debug=True)